In [60]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from collections import defaultdict
from collections import Counter
import pickle
import ast

In [2]:
#Useful functions to save and load files in pickle format
def save_dict(obj, name ):
    with open(f'{name}.pickle', 'wb') as f:
        pickle.dump(obj, f)

def load_obj(name ):
    with open(f'{name}.pickle', 'rb') as f:
        return pickle.load(f)

## Import Data

In [3]:
data = pd.read_csv('Reviews.csv', usecols = ['ProductId','Summary','Text'])

In [4]:
data.head()

ProductId                Summary  \
0  B001E4KFG0  Good Quality Dog Food   
1  B00813GRG4      Not as Advertised   
2  B000LQOCH0  "Delight" says it all   
3  B000UA0QIQ         Cough Medicine   
4  B006K2ZZ7K            Great taffy   

                                                Text  
0  I have bought several of the Vitality canned d...  
1  Product arrived labeled as Jumbo Salted Peanut...  
2  This is a confection that has been around a fe...  
3  If you are looking for the secret ingredient i...  
4  Great taffy at a great price.  There was a wid...

In [5]:
#an example of a text that we will have to analyze
data.Text[6745]

"I love juice and I love carbonated beverages, but it is difficult to see this product having a long retail life.<br /><br />Essentially, this is a good drink that doesn't really do anything well.<br /><br />It doesn't taste good enough to be a juice replacement--and is there really a need for a juice replacement?  It might have limited value in camping situations or during other times where small cans make better travelers.<br /><br />It's not exactly a post-workout recovery drink.  Juice would be better.  Minute Maid juice, for instance, has less sugar and carbohydrates, even though Switch doesn't add any sugar.  And there are plenty of other juices that have more nutrients, including Calcium and other vitamins and supplements, including potassium.  So, it's less healthy than most juices.<br /><br />Switch isn't exactly a diet soda because of the natural sugar content comapared to zero sugar in diet drinks.<br /><br />As a regular alternative to sugared soda, it tastes good, but ther

# Analysis of the dataset

In [6]:
print(f'number of unique products: {len(data.ProductId.unique())} \nnumber of total rows in the dataset: {data.shape[0]}')

number of unique products: 74258 
number of total rows in the dataset: 568454


In [7]:
data.groupby('ProductId').count()

Summary  Text
ProductId                
0006641040       37    37
141278509X        1     1
2734888454        2     2
2841233731        1     1
7310172001      173   173
...             ...   ...
B009UOFTUI        1     1
B009UOFU20        1     1
B009UUS05I        1     1
B009WSNWC4        1     1
B009WVB40S        1     1

[74258 rows x 2 columns]

In [8]:
data.info() 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 568454 entries, 0 to 568453
Data columns (total 3 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   ProductId  568454 non-null  object
 1   Summary    568427 non-null  object
 2   Text       568454 non-null  object
dtypes: object(3)
memory usage: 13.0+ MB


useful: https://towardsdatascience.com/clustering-documents-with-python-97314ad6a78d 

also: https://medium.com/@lucasdesa/text-clustering-with-k-means-a039d84a941b

# 1. Preprocessing

This pre-processing stage refers to the series of treatments that must be done to the corpus so that it can be well represented by statistic model before it’s fed to the K-Means algorithm. The pre-processing routine is divided as such:
- **Corpus tokenization**, that is, divide the different texts into individual words.
- **Stop words removal**, which are common words (a, the, not, etc) that bring close to no contribution to the semantic meaning of a text
- **Noise removal** from the texts, that means basically anything that can’t be recongnized as a english word, such as words with non ASCII symbols, words together with numbers, etc.
- **Stemming**, which reduces a word to it’s root. 


In [9]:
import nltk
import re

from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import RegexpTokenizer

In [10]:
def pre_processing_data(text):           
    
    stop_words = set(stopwords.words('english'))
    text = (text.lower()).replace('\\n',' ')        #converts to lower case and removes extra space
    
    text = text.replace("\r","")
    text = text.replace("\n","")
    text = text.replace("<br />","")
    
    text = text.encode("ascii", "ignore")            #removes non ASCII characters
    text = text.decode()
    
    punctuation = RegexpTokenizer(r'\w+')               #identifies punctuation
    tokens = punctuation.tokenize(text)               #create a list of all words

    ps = PorterStemmer()

    filtered_text = []
    for word in tokens:
        if word not in stop_words:
            filtered_text.append(ps.stem(word))
    
    return filtered_text

### All the cells below were runned only the FIRST time and then saved into a csv file for easier access

`wordlist = data['Text'].apply(lambda text: pre_processing_data(text))`

`data['text_words'] = wordlist`

In [86]:
data.head(10)

ProductId                                        Summary  \
0  B001E4KFG0                          Good Quality Dog Food   
1  B00813GRG4                              Not as Advertised   
2  B000LQOCH0                          "Delight" says it all   
3  B000UA0QIQ                                 Cough Medicine   
4  B006K2ZZ7K                                    Great taffy   
5  B006K2ZZ7K                                     Nice Taffy   
6  B006K2ZZ7K  Great!  Just as good as the expensive brands!   
7  B006K2ZZ7K                         Wonderful, tasty taffy   
8  B000E7L2R4                                     Yay Barley   
9  B00171APVA                               Healthy Dog Food   

                                                Text  \
0  I have bought several of the Vitality canned d...   
1  Product arrived labeled as Jumbo Salted Peanut...   
2  This is a confection that has been around a fe...   
3  If you are looking for the secret ingredient i...   
4  Great taffy at a great price.  There was a wid...   
5  I got a wild hair for taffy and ordered this f...   
6  This saltwater taffy had great flavors and was...   
7  This taffy is so good.  It is very soft and ch...   
8  Right now I'm mostly just sprouting this so my...   
9  This is a very healthy dog food. Good for thei...   

                                          text_words  
0  [bought, sever, vital, can, dog, food, product...  
1  [product, arriv, label, jumbo, salt, peanut, p...  
2  [confect, around, centuri, light, pillowi, cit...  
3  [look, secret, ingredi, robitussin, believ, fo...  
4  [great, taffi, great, price, wide, assort, yum...  
5  [got, wild, hair, taffi, order, five, pound, b...  
6  [saltwat, taffi, great, flavor, soft, chewi, c...  
7  [taffi, good, soft, chewi, flavor, amaz, would...  
8  [right, mostli, sprout, cat, eat, grass, love,...  
9  [healthi, dog, food, good, digest, also, good,...

`data.to_csv('clean_dataset.csv')`

## 2. Create a vocabulary with all the unique words from text_words

In [11]:
#to import directly the filtered dataset instead of pre-process everything again
data = pd.read_csv('clean_dataset.csv')
data.drop('Unnamed: 0',axis=1,inplace=True)

#to mantain the format of text_words as a list and not as a string
data['text_words'] = data['text_words'].map(ast.literal_eval)

In [12]:
data

ProductId                             Summary  \
0       B001E4KFG0               Good Quality Dog Food   
1       B00813GRG4                   Not as Advertised   
2       B000LQOCH0               "Delight" says it all   
3       B000UA0QIQ                      Cough Medicine   
4       B006K2ZZ7K                         Great taffy   
...            ...                                 ...   
568449  B001EO7N10                 Will not do without   
568450  B003S1WTCU                        disappointed   
568451  B004I613EE            Perfect for our maltipoo   
568452  B004I613EE  Favorite Training and reward treat   
568453  B001LR2CU2                         Great Honey   

                                                     Text  \
0       I have bought several of the Vitality canned d...   
1       Product arrived labeled as Jumbo Salted Peanut...   
2       This is a confection that has been around a fe...   
3       If you are looking for the secret ingredient i...   
4       Great taffy at a great price.  There was a wid...   
...                                                   ...   
568449  Great for sesame chicken..this is a good if no...   
568450  I'm disappointed with the flavor. The chocolat...   
568451  These stars are small, so you can give 10-15 o...   
568452  These are the BEST treats for training and rew...   
568453  I am very satisfied ,product is as advertised,...   

                                               text_words  
0       [bought, sever, vital, can, dog, food, product...  
1       [product, arriv, label, jumbo, salt, peanut, p...  
2       [confect, around, centuri, light, pillowi, cit...  
3       [look, secret, ingredi, robitussin, believ, fo...  
4       [great, taffi, great, price, wide, assort, yum...  
...                                                   ...  
568449  [great, sesam, chicken, good, better, restur, ...  
568450  [disappoint, flavor, chocol, note, especi, wea...  
568451  [star, small, give, 10, 15, one, train, sessio...  
568452  [best, treat, train, reward, dog, good, groom,...  
568453  [satisfi, product, advertis, use, cereal, raw,...  

[568454 rows x 4 columns]

In [13]:
def build_dictionary(df):                            

    vocabulary_list = []
    vocabs_in_reviews = defaultdict(list)

    for i in range(len(df)):

        text_filtered = df['text_words'][i]
        
        vocabs_review_i=set()
        for word in text_filtered:
            vocabs_review_i.add(word)

        vocabulary_list.append(vocabs_review_i)
        vocabs_in_reviews[i]=list(vocabs_review_i)

    bag_of_words = set.union(*vocabulary_list)
    
    dictionary = {}
    for num, word in enumerate(bag_of_words):
        dictionary[word] = num
    
    return dictionary

`dictionary = build_dictionary(data)`   -    to build

`save_dict(dictionary,'dictionary')` - to save

In [14]:
dictionary = load_obj('dictionary')   #to load it back

In [15]:
len(dictionary)

109234

## 3. For every unique product ID combine the list of words from different reviews together 

In [16]:
products = list([data.ProductId[i] for i in range(len(data))])
unique_products = list(dict.fromkeys(products))

In [17]:
print(len(products))
print(len(unique_products))

568454
74258


In [98]:
new_data = dict.fromkeys(unique_products)

for product in unique_products:
    index = (np.where(data['ProductId']==product))[0].tolist()

    reviews = []
    for i in index:
        text = data['text_words'][i]
        reviews += text
    
    new_data[product] = reviews

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062


3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705


5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339
5340
5341
5342
5343
5344
5345
5346
5347
5348
5349


6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977
6978
6979
6980
6981
6982
6983
6984
6985
6986
6987
6988
6989
6990
6991
6992
6993
6994
6995
6996


...

67567
67568
67569
67570
67571
67572
67573
67574
67575
67576
67577
67578
67579
67580
67581
67582
67583
67584
67585
67586
67587
67588
67589
67590
67591
67592
67593
67594
67595
67596
67597
67598
67599
67600
67601
67602
67603
67604
67605
67606
67607
67608
67609
67610
67611
67612
67613
67614
67615
67616
67617
67618
67619
67620
67621
67622
67623
67624
67625
67626
67627
67628
67629
67630
67631
67632
67633
67634
67635
67636
67637
67638
67639
67640
67641
67642
67643
67644
67645
67646
67647
67648
67649
67650
67651
67652
67653
67654
67655
67656
67657
67658
67659
67660
67661
67662
67663
67664
67665
67666
67667
67668
67669
67670
67671
67672
67673
67674
67675
67676
67677
67678
67679
67680
67681
67682
67683
67684
67685
67686
67687
67688
67689
67690
67691
67692
67693
67694
67695
67696
67697
67698
67699
67700
67701
67702
67703
67704
67705
67706
67707
67708
67709
67710
67711
67712
67713
67714
67715
67716
67717
67718
67719
67720
67721
67722
67723
67724
67725
67726
67727
67728
67729
67730
67731
67732
6773

68935
68936
68937
68938
68939
68940
68941
68942
68943
68944
68945
68946
68947
68948
68949
68950
68951
68952
68953
68954
68955
68956
68957
68958
68959
68960
68961
68962
68963
68964
68965
68966
68967
68968
68969
68970
68971
68972
68973
68974
68975
68976
68977
68978
68979
68980
68981
68982
68983
68984
68985
68986
68987
68988
68989
68990
68991
68992
68993
68994
68995
68996
68997
68998
68999
69000
69001
69002
69003
69004
69005
69006
69007
69008
69009
69010
69011
69012
69013
69014
69015
69016
69017
69018
69019
69020
69021
69022
69023
69024
69025
69026
69027
69028
69029
69030
69031
69032
69033
69034
69035
69036
69037
69038
69039
69040
69041
69042
69043
69044
69045
69046
69047
69048
69049
69050
69051
69052
69053
69054
69055
69056
69057
69058
69059
69060
69061
69062
69063
69064
69065
69066
69067
69068
69069
69070
69071
69072
69073
69074
69075
69076
69077
69078
69079
69080
69081
69082
69083
69084
69085
69086
69087
69088
69089
69090
69091
69092
69093
69094
69095
69096
69097
69098
69099
69100
6910

70303
70304
70305
70306
70307
70308
70309
70310
70311
70312
70313
70314
70315
70316
70317
70318
70319
70320
70321
70322
70323
70324
70325
70326
70327
70328
70329
70330
70331
70332
70333
70334
70335
70336
70337
70338
70339
70340
70341
70342
70343
70344
70345
70346
70347
70348
70349
70350
70351
70352
70353
70354
70355
70356
70357
70358
70359
70360
70361
70362
70363
70364
70365
70366
70367
70368
70369
70370
70371
70372
70373
70374
70375
70376
70377
70378
70379
70380
70381
70382
70383
70384
70385
70386
70387
70388
70389
70390
70391
70392
70393
70394
70395
70396
70397
70398
70399
70400
70401
70402
70403
70404
70405
70406
70407
70408
70409
70410
70411
70412
70413
70414
70415
70416
70417
70418
70419
70420
70421
70422
70423
70424
70425
70426
70427
70428
70429
70430
70431
70432
70433
70434
70435
70436
70437
70438
70439
70440
70441
70442
70443
70444
70445
70446
70447
70448
70449
70450
70451
70452
70453
70454
70455
70456
70457
70458
70459
70460
70461
70462
70463
70464
70465
70466
70467
70468
7046

71676
71677
71678
71679
71680
71681
71682
71683
71684
71685
71686
71687
71688
71689
71690
71691
71692
71693
71694
71695
71696
71697
71698
71699
71700
71701
71702
71703
71704
71705
71706
71707
71708
71709
71710
71711
71712
71713
71714
71715
71716
71717
71718
71719
71720
71721
71722
71723
71724
71725
71726
71727
71728
71729
71730
71731
71732
71733
71734
71735
71736
71737
71738
71739
71740
71741
71742
71743
71744
71745
71746
71747
71748
71749
71750
71751
71752
71753
71754
71755
71756
71757
71758
71759
71760
71761
71762
71763
71764
71765
71766
71767
71768
71769
71770
71771
71772
71773
71774
71775
71776
71777
71778
71779
71780
71781
71782
71783
71784
71785
71786
71787
71788
71789
71790
71791
71792
71793
71794
71795
71796
71797
71798
71799
71800
71801
71802
71803
71804
71805
71806
71807
71808
71809
71810
71811
71812
71813
71814
71815
71816
71817
71818
71819
71820
71821
71822
71823
71824
71825
71826
71827
71828
71829
71830
71831
71832
71833
71834
71835
71836
71837
71838
71839
71840
71841
7184

73047
73048
73049
73050
73051
73052
73053
73054
73055
73056
73057
73058
73059
73060
73061
73062
73063
73064
73065
73066
73067
73068
73069
73070
73071
73072
73073
73074
73075
73076
73077
73078
73079
73080
73081
73082
73083
73084
73085
73086
73087
73088
73089
73090
73091
73092
73093
73094
73095
73096
73097
73098
73099
73100
73101
73102
73103
73104
73105
73106
73107
73108
73109
73110
73111
73112
73113
73114
73115
73116
73117
73118
73119
73120
73121
73122
73123
73124
73125
73126
73127
73128
73129
73130
73131
73132
73133
73134
73135
73136
73137
73138
73139
73140
73141
73142
73143
73144
73145
73146
73147
73148
73149
73150
73151
73152
73153
73154
73155
73156
73157
73158
73159
73160
73161
73162
73163
73164
73165
73166
73167
73168
73169
73170
73171
73172
73173
73174
73175
73176
73177
73178
73179
73180
73181
73182
73183
73184
73185
73186
73187
73188
73189
73190
73191
73192
73193
73194
73195
73196
73197
73198
73199
73200
73201
73202
73203
73204
73205
73206
73207
73208
73209
73210
73211
73212
7321

`save_dict(new_data,'new_data')` - to save

In [18]:
reviews_per_product = load_obj('new_data') #to load

In [36]:
reviews_per_product['0006641040']

['day',
 'person',
 'say',
 'chicken',
 'soup',
 'probabl',
 'go',
 'follow',
 'word',
 'soul',
 'mayb',
 'teenag',
 'soul',
 'use',
 'way',
 'rememb',
 'time',
 'person',
 'said',
 'chicken',
 'soup',
 'word',
 'follow',
 'enthusiast',
 'rice',
 'power',
 'mauric',
 'sendak',
 'catchi',
 '1962',
 'children',
 'book',
 'pleas',
 'report',
 'care',
 'read',
 'book',
 'today',
 'find',
 'dimish',
 'jot',
 'term',
 'frolicksom',
 'fun',
 'book',
 'led',
 'whirlwind',
 'chicken',
 'soup',
 'year',
 'host',
 'boy',
 'bear',
 'littl',
 'resembl',
 'sendak',
 'great',
 'rhyme',
 'tale',
 'pierr',
 'look',
 'demeanor',
 'catchi',
 'flounci',
 'bounci',
 'combo',
 'soup',
 'peopl',
 'love',
 'ostens',
 'book',
 'meant',
 'teach',
 'children',
 'differ',
 'month',
 'year',
 'month',
 'get',
 'rhythmic',
 'poem',
 'accompani',
 'illustr',
 'fairli',
 'simpl',
 'pen',
 'ink',
 'draw',
 'occasion',
 'splash',
 'blue',
 'vari',
 'shade',
 'yellow',
 'gray',
 'green',
 'may',
 'wonder',
 'author',
 '

In [20]:
len(reviews_per_product)

74258

## For every productID calculate a vector in which each element corresponds to a word in the dictionary and the values are given by the TF-IDF score of that word in that document

In [21]:
frequency_of_word = []
for key, item in reviews_per_product.items():
    frequency_of_words = Counter(item)
    frequency_of_word.append(frequency_of_words)
frequency_of_word

[Counter({'bought': 1,
          'sever': 1,
          'vital': 1,
          'can': 1,
          'dog': 1,
          'food': 1,
          'product': 3,
          'found': 1,
          'good': 1,
          'qualiti': 1,
          'look': 1,
          'like': 1,
          'stew': 1,
          'process': 1,
          'meat': 1,
          'smell': 1,
          'better': 2,
          'labrador': 1,
          'finicki': 1,
          'appreci': 1}),
 Counter({'product': 2,
          'arriv': 1,
          'label': 1,
          'jumbo': 2,
          'salt': 1,
          'peanut': 2,
          'actual': 1,
          'small': 1,
          'size': 1,
          'unsalt': 1,
          'sure': 1,
          'error': 1,
          'vendor': 1,
          'intend': 1,
          'repres': 1}),
 Counter({'confect': 1,
          'around': 1,
          'centuri': 1,
          'light': 1,
          'pillowi': 1,
          'citru': 1,
          'gelatin': 1,
          'nut': 1,
          'case': 1,
          'f

In [22]:
len(frequency_of_word)

74258

In [44]:
def frequency(vocabulary,frequency_of_word):
    f = defaultdict()
    for word in vocabulary.keys():
        f[word] = sum(frequency_of_word[i][word] for i in range(len(frequency_of_word)) if word in frequency_of_word[i])
    return f   

`freq = frequency(dictionary,frequency_of_word)`

`save_dict(freq,'frequencies')` - to save

In [23]:
frequencies = load_obj('frequencies') #to load

In [24]:
frequencies

defaultdict(None,
            {'piti': 248,
             'b005g0f8ri': 1,
             'lorri': 1,
             'intensivo': 2,
             'b000f4d5gc': 2,
             'johnvisnaska': 1,
             'cearal': 4,
             'smartpost': 4,
             'vitner': 1,
             'terrrif': 1,
             'scrutin': 27,
             'surpriseh': 1,
             'aroma': 9532,
             'golit': 3,
             'espaci': 1,
             'b004nneyuc': 3,
             '19gfiber': 1,
             'keuriq': 5,
             'creapur': 1,
             'b001f2ayh6': 1,
             'familyus': 1,
             'sodiumgranul': 1,
             '7y': 2,
             'hilacha': 1,
             'price': 87414,
             'linchi': 2,
             'acquies': 1,
             'glycogen': 20,
             'oookaaay': 1,
             'mebe': 1,
             'valuu': 1,
             'tikyada': 1,
             'b000lktbdq': 3,
             'bove': 3,
             'brugger': 1,
             'jedi':

In [25]:
print('max: ',max(list(frequencies.values())))
print('min: ',min(list(frequencies.values())))

max:  288508
min:  1


In [26]:
def filter_words(frequencies):
    
    useful_words = []                                 #list that contains all the words that we think are useful for clustering
    frequent_words = []                               #list that contains all the words over a certain treshold 

    for key, value in frequencies.items():
        if value > 20 and value < 200000:             #we decided to only consider the words that are inside this range of frewuencies 
            useful_words.append(key)
        elif value > 200000:
            frequent_words.append(key)
    
    return(useful_words, frequent_words)
        
useful_words = filter_words(frequencies)[0]
frequent_words = filter_words(frequencies)[1]

By doing this we will reduce the length of the dictionary that will contain all the different unique words found inside the reviews. we noticed that words with very low frequencies are pretty rare or they could be wrong words, with spelling mistakes, hence, with no meaning.
The length will go from `len(dictionary) = 109234 ` to `len(useful_words) = 14783 `

In [27]:
frequent_words

['product', 'good', 'tast', 'flavor', 'like']

As we can see above, all the words with very high frequencies are very common words, so they will not be useful in the determination of the cluster in which a certain review will belong

In [28]:
def new_dictionary(useful_words):
    
    dictionary = defaultdict()
    
    for i, word in enumerate(useful_words):
        dictionary[word] = i
    
    return dictionary

dictionary_filtered = new_dictionary(useful_words)

In [29]:
dictionary_filtered

defaultdict(None,
            {'piti': 0,
             'scrutin': 1,
             'aroma': 2,
             'price': 3,
             'agress': 4,
             'turf': 5,
             'tantrum': 6,
             'theater': 7,
             'bentley': 8,
             'superbl': 9,
             'shea': 10,
             'vest': 11,
             'american': 12,
             'gurgl': 13,
             'dial': 14,
             'dusti': 15,
             'loooong': 16,
             'terra': 17,
             'evang': 18,
             'immens': 19,
             'alreadi': 20,
             'sauc': 21,
             'slump': 22,
             'activ': 23,
             'capabl': 24,
             '9x13': 25,
             'confer': 26,
             'ys': 27,
             'nestl': 28,
             'amazonian': 29,
             'toy': 30,
             'rip': 31,
             'presum': 32,
             'nutro': 33,
             'circl': 34,
             'samsclub': 35,
             'ritual': 36,
             '

Now we want to create a matrix that will have the following structure:
- each column will represent one word from the list **useful_words**
- each row represents a different unique product id

Each **cell** of the matrix will represent the frequence of that certain word inside the reviews of that certain product

In [38]:
matrix = np.zeros((len(unique_products),len(dictionary_filtered)))
for i, product in enumerate(unique_products):      #per ogni prodotto con indice i   
    for word,j in dictionary_filtered.items():          #per ogni parola con indice j nel dizionario
        if word in frequency_of_word[i].keys():        #se la parola si trova nel dizionario di frequenze del prodotto
            matrix[i][j] += frequency_of_word[i][word]

In [68]:
matrix.shape

(74258, 14783)

In [73]:
a = np.zeros((len(unique_products),len(dictionary_filtered)))
a

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

### Singular Value Decomposition

In [ ]:
import sklearn
from sklearn.pipeline import make_pipeline
from sklearn.decomposition import TruncatedSVD
from sklearn.preprocessing import Normalizer

In [87]:
svd = TruncatedSVD(n_components = 70,n_iter=3, random_state=42)
svd.fit(matrix)

TruncatedSVD(n_components=100, n_iter=3, random_state=42)

In [62]:
# normalizer = Normalizer(copy=False)
# lsa = make_pipeline(svd, normalizer)

# X = lsa.fit_transform(matrix)

In [63]:
X

array([[ 1.91405987e-01, -2.04254780e-01,  1.96792811e-01, ...,
        -1.92225450e-03, -1.46938424e-02, -1.12664450e-03],
       [ 6.96184022e-02, -5.37265180e-02, -1.24279251e-02, ...,
         2.84961852e-03,  1.77445801e-02,  9.61554141e-07],
       [ 1.07707782e-01, -9.76083079e-02,  3.83546718e-02, ...,
        -5.20633782e-02, -4.53676231e-03, -1.35557111e-03],
       ...,
       [ 2.14362470e-01, -6.64277078e-02, -5.40521391e-02, ...,
         3.08035826e-02, -3.64449996e-02, -8.25603498e-03],
       [ 3.40778707e-01, -3.72501800e-01,  3.29909345e-01, ...,
         8.44883285e-05,  9.92730354e-03,  4.05980478e-03],
       [ 1.06759632e-01, -3.43377031e-02, -4.36783261e-02, ...,
         3.67312357e-02, -1.57720124e-02,  1.22363007e-03]])

In [88]:
explained_variance = svd.explained_variance_ratio_.sum()
print("Explained variance of the SVD step: {}%".format(int(explained_variance * 100)))

Explained variance of the SVD step: 91%


In [89]:
svd.components_.shape

(100, 14783)

In [90]:
svd.singular_values_

array([14075.00253347,  9413.25706533,  6734.25180712,  5593.33577998,
        5539.76174194,  5249.74516222,  4378.8704711 ,  4032.0961473 ,
        3456.09735357,  3418.55320415,  3357.42962521,  3186.4630012 ,
        3067.33959025,  2782.73433076,  2678.44758556,  2519.12943131,
        2451.48194795,  2382.96328498,  2339.29088484,  2277.59855353,
        2203.46669602,  2132.84021296,  2100.65274925,  2030.53640809,
        1994.16107749,  1948.3513788 ,  1826.08344761,  1824.37496081,
        1742.82688773,  1701.37954768,  1657.06326747,  1623.21672812,
        1598.6251558 ,  1573.88429105,  1525.61123708,  1493.74563693,
        1430.42526789,  1421.72440954,  1416.05025095,  1363.51233843,
        1346.81030917,  1319.56670258,  1298.14912459,  1272.90815625,
        1259.65363354,  1246.39113587,  1219.70434627,  1205.4849827 ,
        1201.06396469,  1178.06534107,  1160.37365456,  1149.61918447,
        1128.03692187,  1121.30834436,  1111.77728878,  1098.67074959,
      

In [83]:
(svd.singular_values_).shape

(1000,)

In [ ]:
components = svd.components_
features = useful_words
print(components.shape)
components[0]

In [ ]:
components_features = {i: [] for i in range(len(components))} 
n_comp = len(components)
for i in range(n_comp):
    ith_comp = components[i]
    for coef,feat in zip(ith_comp,features):
        if  coef > 10**(-2):
            components_features[i].append(feat)

In [ ]:
relevant_words = set(list(components_features.values())[0])
print(len(relevant_words))
print(relevant_words)

## 5. Calculate Tf-Idf Scores for each word inside the reviews of a product ID

In [106]:
def tf(frequency_of_word,review_per_products):      
 
    tfs = []

    for i, item in enumerate(reviews_per_product.items()):
        text_filtered = reviews_per_product[item[0]]

        tf = dict.fromkeys(text_filtered,0)
        tot_number_of_words = len(text_filtered)

        for key,item in frequency_of_word[i].items():
            frequency = item
            tf_score = frequency / tot_number_of_words
            tf[key] = tf_score    
        tfs.append(tf)
        
    return tfs

In [108]:
def idf(dictionary,frequency_of_word,reviews_per_product):    
    
    N = len(reviews_per_product)
    idf = dict.fromkeys(dictionary.keys(), 0)

    #calculate df by looking at the number of documents each token appears
    for i in range(len(reviews_per_product)):
        for key,item in frequency_of_word[i].items():
            if item > 0:
                idf[key] += 1
                
    #calculate idf 
    for key,item in idf.items():
        idf[key] = np.log(N/(item))
        
    return idf

In [110]:
def tf_idf_score(tf_score,idf_score,reviews_per_product):    

    tf_idf_scores = []
    for i in range(len(reviews_per_product)):
        tf_idf_score = {}
        for key,item in tf_score[i].items():
            tf_idf_score[key] = round(item*idf_score[key],5) 
        tf_idf_scores.append(tf_idf_score)

    return tf_idf_scores

In [107]:
tf_score = tf(frequency_of_word,reviews_per_product)

In [109]:
idf_score = idf(dictionary,frequency_of_word,reviews_per_product)

In [111]:
tf_idf_scores = tf_idf_score(tf_score,idf_score,reviews_per_product)

In [112]:
save_dict(tf_idf_scores,'tf_idf_scores')    #to save

In [29]:
tf_idf_scores = load_obj('tf_idf_scores')   #to load

## 6. Associo ad ogni product ID una lista di scores:
- 0 se la parola non è presente
- tf-idf score di quella parola in quel productID